In [3]:
import requests
import re
import pandas as pd
import io

In [2]:
# Function to download climate data for a specific variable, year, and month for Virginia
def nclim_download_for_VA(var_name, year, month, url_root='https://www.ncei.noaa.gov/data/nclimgrid-daily/access/averages/'):
    
    filename = '-'.join([var_name, str(year) + str(month).zfill(2), 'cty', 'scaled.csv'])
    
    # Get response from server
    response = requests.get(url_root + str(year) +  '/' + filename)
    
    if response.status_code == 200:
        # Converting the content to DataFrame without considering the first row as header
        data = pd.read_csv(io.StringIO(response.content.decode('utf-8')), header=None)
        print(data)
        #data.drop(['0','5'])
        # Filtering rows with third column "VA:"
        va_data = data[data[2].str.contains("VA:", na=False)]
        
        va_filename = "VA_" + filename
        cols=["cty","stationId","county","year","month","dtype","1","2","3","4","5","6","7","8","9","10","11","12","13","14","15","16","17","18","19","20","21","22","23","24","25","26","27","28","29","30","31"]
        va_data.to_csv("/Users/saideepak/Documents/Daen 690/VAfinal" + va_filename, index=False, header=cols)
    else:
        print('Failed to download ' + filename)
    
    return None




In [3]:
# Columns representing different climate variables
cols = ['prcp','tavg','tmin','tmax']

In [5]:
# Looping over years and months to download data for each climate variable
for y in range(1950,2024):
    for m in range(1,13):
        for col in cols:
            nclim_download_for_VA(col,str(y),str(m))



Failed to download prcp-195001-cty-scaled.csv
Failed to download tavg-195001-cty-scaled.csv
Failed to download tmin-195001-cty-scaled.csv
Failed to download tmax-195001-cty-scaled.csv
Failed to download prcp-195002-cty-scaled.csv
Failed to download tavg-195002-cty-scaled.csv
Failed to download tmin-195002-cty-scaled.csv
Failed to download tmax-195002-cty-scaled.csv
Failed to download prcp-195003-cty-scaled.csv
Failed to download tavg-195003-cty-scaled.csv
Failed to download tmin-195003-cty-scaled.csv
Failed to download tmax-195003-cty-scaled.csv
Failed to download prcp-195004-cty-scaled.csv
Failed to download tavg-195004-cty-scaled.csv
Failed to download tmin-195004-cty-scaled.csv
Failed to download tmax-195004-cty-scaled.csv
Failed to download prcp-195005-cty-scaled.csv
Failed to download tavg-195005-cty-scaled.csv
Failed to download tmin-195005-cty-scaled.csv
Failed to download tmax-195005-cty-scaled.csv
Failed to download prcp-195006-cty-scaled.csv
Failed to download tavg-195006-cty

In [22]:
# Function to concatenate data files into a single DataFrame
def concat_datasets(year_range, month_range, cols, file_path_root="/Users/saideepak/Documents/Daen 690/"):
    all_data = []
    # Looping through each file and appending to a list
    for y in year_range:
        for m in month_range:
            for col in cols:
                filename = f"VAfinalVA_{col}-{str(y)}{str(m).zfill(2)}-cty-scaled.csv"
                file_path = file_path_root + filename
                try:
                    data = pd.read_csv(file_path)
                    all_data.append(data)
                except FileNotFoundError:
                    print(f"File {filename} not found!")
    # Concatenating all data into a single DataFrame
    concatenated_data = pd.concat(all_data, axis=0, ignore_index=True)
    concatenated_filename = file_path_root + "VAfinalVA_concatenated.csv"
    concatenated_data.to_csv(concatenated_filename, index=False)
    print(f"Concatenated data saved to {concatenated_filename}")

# Running the concatenation function
concat_datasets(year_range=range(1950, 2024), month_range=range(1, 13), cols=['prcp', 'tavg', 'tmin', 'tmax'])


File VAfinalVA_prcp-195001-cty-scaled.csv not found!
File VAfinalVA_tavg-195001-cty-scaled.csv not found!
File VAfinalVA_tmin-195001-cty-scaled.csv not found!
File VAfinalVA_tmax-195001-cty-scaled.csv not found!
File VAfinalVA_prcp-195002-cty-scaled.csv not found!
File VAfinalVA_tavg-195002-cty-scaled.csv not found!
File VAfinalVA_tmin-195002-cty-scaled.csv not found!
File VAfinalVA_tmax-195002-cty-scaled.csv not found!
File VAfinalVA_prcp-195003-cty-scaled.csv not found!
File VAfinalVA_tavg-195003-cty-scaled.csv not found!
File VAfinalVA_tmin-195003-cty-scaled.csv not found!
File VAfinalVA_tmax-195003-cty-scaled.csv not found!
File VAfinalVA_prcp-195004-cty-scaled.csv not found!
File VAfinalVA_tavg-195004-cty-scaled.csv not found!
File VAfinalVA_tmin-195004-cty-scaled.csv not found!
File VAfinalVA_tmax-195004-cty-scaled.csv not found!
File VAfinalVA_prcp-195005-cty-scaled.csv not found!
File VAfinalVA_tavg-195005-cty-scaled.csv not found!
File VAfinalVA_tmin-195005-cty-scaled.csv not 

In [4]:
data = pd.read_csv("/Users/saideepak/Documents/Daen 690/VAfinalVA_concatenated.csv")
# Step 1: Melt the dataset
melted_df = data.melt(id_vars=['cty', 'stationId', 'county', 'year', 'month', 'dtype'], 
                      value_vars=[str(i) for i in range(1, 32)], 
                      var_name='day', 
                      value_name='value')

# Step 2: Convert year, month, and day into a single date column
melted_df['date'] = pd.to_datetime(melted_df[['year', 'month']].assign(DAY=melted_df['day']), errors='coerce')

# Step 3: Pivot the dataframe
pivoted_df = melted_df.pivot_table(index=['cty', 'stationId', 'county', 'date'], 
                                  columns='dtype', 
                                  values='value', 
                                  aggfunc='first').reset_index()

# Step 4: Filter out invalid dates
valid_dates_df = pivoted_df.dropna(subset=['date'])

# Step 5: Sort by date
sorted_df = valid_dates_df.sort_values(by='date')

# Display the first few rows of the transformed dataset
sorted_df.head()


dtype    cty  stationId                   county       date  PRCP  TAVG  TMAX  \
0        cty      44001      VA: Accomack County 1951-01-01   0.0  2.17  6.04   
2869668  cty      44640           VA: Galax city 1951-01-01   0.0 -3.74  0.95   
2843097  cty      44630  VA: Fredericksburg city 1951-01-01   0.0 -0.21  6.13   
345423   cty      44027      VA: Buchanan County 1951-01-01   0.0 -3.39  1.60   
2816526  cty      44620        VA: Franklin city 1951-01-01   0.0  2.68  8.44   

dtype    TMIN  
0       -1.71  
2869668 -8.43  
2843097 -6.54  
345423  -8.38  
2816526 -3.07

In [5]:
sorted_df.tail()

dtype    cty  stationId                county       date  PRCP   TAVG   TMAX  \
2497673  cty      44197      VA: Wythe County 2023-09-30  0.00  17.02  24.52   
2524244  cty      44199       VA: York County 2023-09-30  0.86  18.91  20.66   
2550815  cty      44510   VA: Alexandria city 2023-09-30  0.00  18.75  20.93   
2603957  cty      44530  VA: Buena Vista city 2023-09-30  0.00  18.86  24.54   
3507371  cty      44840   VA: Winchester city 2023-09-30  0.00  17.11  20.91   

dtype     TMIN  
2497673   9.51  
2524244  17.16  
2550815  16.56  
2603957  13.17  
3507371  13.31

In [28]:
file_path = "/Users/saideepak/Documents/Daen 690/sorted_data.csv"
sorted_df.to_csv(file_path, index=False)

In [29]:
sorted_df.tail()

dtype    cty  stationId                county       date  PRCP   TAVG   TMAX  \
2497673  cty      44197      VA: Wythe County 2023-09-30  0.00  17.02  24.52   
2524244  cty      44199       VA: York County 2023-09-30  0.86  18.91  20.66   
2550815  cty      44510   VA: Alexandria city 2023-09-30  0.00  18.75  20.93   
2603957  cty      44530  VA: Buena Vista city 2023-09-30  0.00  18.86  24.54   
3507371  cty      44840   VA: Winchester city 2023-09-30  0.00  17.11  20.91   

dtype     TMIN  
2497673   9.51  
2524244  17.16  
2550815  16.56  
2603957  13.17  
3507371  13.31

In [6]:
# Save the dataframe as a GZIP compressed CSV file
compression_file_path = "/Users/saideepak/Documents/Daen 690/sorted_data_compressed.csv.gz"
sorted_df.to_csv(compression_file_path, index=False, compression="gzip")


In [31]:
# Verifying the compressed data by loading and displaying the last few rows
test_df = pd.read_csv(compression_file_path, compression='gzip')
print(test_df.tail())

         cty  stationId                county        date  PRCP   TAVG   TMAX  \
3507367  cty      44197      VA: Wythe County  2023-09-30  0.00  17.02  24.52   
3507368  cty      44199       VA: York County  2023-09-30  0.86  18.91  20.66   
3507369  cty      44510   VA: Alexandria city  2023-09-30  0.00  18.75  20.93   
3507370  cty      44530  VA: Buena Vista city  2023-09-30  0.00  18.86  24.54   
3507371  cty      44840   VA: Winchester city  2023-09-30  0.00  17.11  20.91   

          TMIN  
3507367   9.51  
3507368  17.16  
3507369  16.56  
3507370  13.17  
3507371  13.31  
